<a href="https://colab.research.google.com/github/JSchoonmaker/blockchain_projects/blob/main/Flipside_crypto_CryptoPunks_data.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# installing this pkg helps with unnesting some of the json returned from Flipside
pip install flat-table

In [2]:
%load_ext google.colab.data_table
import requests
import pandas as pd
import flat_table
import json

In [7]:
url = ('https://api.flipsidecrypto.com/api/v2/queries/99990404-5727-40cb-989a-f9d66738bdca/data/latest')

response = requests.get(url)  

print(f"Request returned {response.status_code} : '{response.reason}'")

payload = response.json()

import pprint
pp = pprint.PrettyPrinter(indent=1)
pp.pprint(payload[0])

https://api.flipsidecrypto.com/api/v2/queries/99990404-5727-40cb-989a-f9d66738bdca/data/latest
Request returned 200 : 'OK'
{'BLOCK_ID': 10912473,
 'BLOCK_TIMESTAMP': '2020-09-22T13:10:15Z',
 'CONTRACT_ADDRESS': '0xb47e3cd837ddf8e4c57f05d70ab865de6e193bbb',
 'CONTRACT_NAME': 'cryptopunks c token',
 'EVENT_INDEX': 292,
 'EVENT_INPUTS': '{\n'
                 '  "fromAddress": '
                 '"0x5f7190b7943858b7bdd24f069241612091c6a986",\n'
                 '  "punkIndex": 1684,\n'
                 '  "toAddress": '
                 '"0x8dbbca57ea56290efa14d835bbfd34faf1d89753",\n'
                 '  "value": 40000000000000000000\n'
                 '}',
 'EVENT_NAME': 'PunkBought',
 'EVENT_REMOVED': False,
 'TX_FROM_ADDRESS': '0x8dbbca57ea56290efa14d835bbfd34faf1d89753',
 'TX_FROM_ADDRESS_NAME': None,
 'TX_FROM_LABEL': None,
 'TX_FROM_LABEL_SUBTYPE': None,
 'TX_FROM_LABEL_TYPE': None,
 'TX_ID': '0x6cc579851dd969f8dd662c0b44ed57c3651c477c78172a846ec252300d2e5f15',
 'TX_SUCCEEDED': Tr

In [8]:
df = pd.json_normalize(payload)

In [9]:
# parsing the column with nested json
df['EVENT_INPUTS'] = df['EVENT_INPUTS'].apply(lambda x:json.loads(x))

In [10]:
df = flat_table.normalize(df)

In [11]:
df

index  ...                    EVENT_INPUTS.fromAddress
0          0  ...  0x5f7190b7943858b7bdd24f069241612091c6a986
1          1  ...  0xef764bac8a438e7e498c2e5fccf0f174c3e3f8db
2          2  ...  0xa7eba7fda7e463c5509519edf03137c57f3ebe73
3          3  ...  0xcf0e9b4746cfb97bae329fe5f696969f6564566a
4          4  ...  0xb40dac2f71aba8ec669f74796b447c9602f0f095
...      ...  ...                                         ...
13329  13329  ...  0x53ede7cae3eb6a7d11429fe589c0278c9acbe21a
13330  13330  ...  0x0eb9a7ff5cbf719251989caf1599c1270eafb531
13331  13331  ...  0x52ad8f3c506aa25b954276c5456060dad6f3fd7b
13332  13332  ...  0xf556cf12807fc720a9b57f54f548d575905a1ed0
13333  13333  ...  0x48db199821bbd5be47c29bb242e3cdf1ef099d7e

[13334 rows x 24 columns]

In [ ]:
# creating a df with only relevant data
df_punks = df[['BLOCK_ID', 'BLOCK_TIMESTAMP', 'EVENT_INDEX', 'EVENT_NAME', 'TX_FROM_ADDRESS', 'EVENT_INPUTS.toAddress', 'EVENT_INPUTS.punkIndex', 'EVENT_INPUTS.fromAddress', 'EVENT_INPUTS.value' ]].copy()

In [ ]:
# converting wei to eth
df_punks['ETH_AMOUNT'] = df_punks['EVENT_INPUTS.value']/1e18

In [ ]:
# data ready for further analysis
df_punks

BLOCK_ID       BLOCK_TIMESTAMP  ...     EVENT_INPUTS.value ETH_AMOUNT
0     10929682  2020-09-25T04:31:27Z  ...   12000000000000000000         12
1     10929954  2020-09-25T05:33:32Z  ...    4990000000000000000       4.99
2     10929995  2020-09-25T05:42:14Z  ...    3290000000000000000       3.29
3     10930084  2020-09-25T06:02:03Z  ...    3890000000000000000       3.89
4     10930128  2020-09-25T06:10:31Z  ...    3490000000000000000       3.49
...        ...                   ...  ...                    ...        ...
9995  12939111  2021-08-01T10:27:53Z  ...   34000000000000000000         34
9996  12939133  2021-08-01T10:34:48Z  ...   34880000000000000000      34.88
9997  12939217  2021-08-01T10:55:29Z  ...   70000000000000000000         70
9998  12939250  2021-08-01T11:03:55Z  ...  145000000000000000000        145
9999  12939296  2021-08-01T11:11:58Z  ...  135000000000000000000        135

[10000 rows x 10 columns]